In [1]:
## Load the packages we will use:
# -------------------
using LinearAlgebra
using Plots
using CSV, DataFrames
using ForwardDiff
using Interpolations, Polynomials

# Helper Functions

In [2]:
function decompose(lambda)
    n = size(lambda)[1] - 2
    a = [lambda[i,i+1] for i = 2:n+1]
    b = [lambda[i,i-1] for i = 3:n+1]
    c = [lambda[i,n+2] / lambda[1,n+2] for i = 2:n]
    d = [lambda[1,i] for i = 2:n+2]

    return a, b, c, d
end

function recompose(a,b,c,d)
    n = length(a)
    lambda = zeros(eltype(c), n+2,n+2)
    for i = 1:n
        lambda[i+1,i+2] = a[i]
    end
    for i = 1:n-1
        lambda[i+2, i+1] = b[i]
    end
    for i = 1:(n+1)
        lambda[1, i+1] = c[i]
    end

    for i = 1:n-1
        for j = i+2:(n+1)
            lambda[i+1,j+1] = d[i] * c[j]
        end
    end
    return lambda
end

function compute_eta(N)
    low = 1.0
    high = 2.0
    for i in 1:50
        mid = (low+high)/2.0
        val = (1+2*N*mid)*(mid-1)^(2*N)
        if val <1
            low = mid
        else
            high =mid
        end
    end
    return low
end

function compute_parts_from_d(eta, r, N, d)
    a = zeros(eltype(d), N)
    b = zeros(eltype(d), N-1)
    c = zeros(eltype(d), N+1)
    c[N+1] = sqrt(2*r)
    c[N] = 2*r*(1+sum(d)+(eta-1)/sqrt(2*r))
    for i in 1:(N-1)
        c[i] = 2*r*(eta*sum(d[1:i]) - d[i]+eta)
    end
    
    a[N] = 1 - sqrt(2*r)*(1+sum(d))
    a[N-1] = 1/eta * (c[N]^2/(2*r) -a[N] - (1+eta)*c[N]*(1+sum(d[1:(N-2)])) + c[N-1]*c[N]/(2*r))
    b[N-1] = 1/eta * ((eta-1)*c[N]^2/(2*r) +(1-eta)*a[N] + c[N]*(1+sum(d[1:(N-2)])) - c[N-1]*c[N]/(2*r))
    for w in 1:(N-3)
        i = N-1-w
        a[i] = 1/eta * (c[i+1]^2/(2*r) + c[i]*c[i+1]/(2*r) - a[i+1] - d[i+1]*(sum(c[(i+3):(N+1)])) -(1+eta)*c[i+1]*(1+sum(d[1:(i-1)])) +b[i+1]*(2*eta-1))
        b[i] = 1/eta * ((eta-1)*c[i+1]^2/(2*r) - c[i]*c[i+1]/(2*r) - (eta-1)*a[i+1] - (eta-1)*d[i+1]*(sum(c[(i+3):(N+1)])) + c[i+1]*(1+sum(d[1:(i-1)])) +(eta-1)*b[i+1]*(2*eta-1))
    end
    a[1] = 1/eta * (c[2]^2/(2*r) + c[1]*c[2]/(2*r) -a[2] - (1+eta)*c[2] -d[2]*sum(c[4:(N+1)]) + b[2]*(2*eta-1))
    b[1] = 1/eta * ((eta-1)*c[2]^2/(2*r) - c[1]*c[2]/(2*r) -(eta-1)*a[2] - (eta-1)*d[2]*sum(c[4:(N+1)]) + c[2] + (eta-1)*b[2]*(2*eta-1))
    return a,b,c
end

function rowSumMinusColumnSumMinusTarget(a,b,c,d,n)
    #Compute the difference of row sums and column sums from the goal
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    target = zeros(eltype(d),n+2)
    target[1]=-1
    target[n+2]=1
    
    target[2:(n+1)] += a[1:n]
    target[3:(n+2)] -= a[1:n]

    target[3:(n+1)] += b[1:(n-1)]
    target[2:n] -= b[1:(n-1)]

    target[1] += sum(c[1:(n+1)])
    target[2:(n+2)] -= c[1:(n+1)]

    for i = 1:n-1
        target[i+1] +=  d[i] * sum(c[i+2:(n+1)])
        target[i+3:(n+2)] -= d[i] * c[i+2:(n+1)]
    end
    #First and last equality are already enforced. They will equal zero for free.
    
    #We can replace first one by the final equality needed for the coefficient of ||g_0|| to be zero
    target[1] = -c[1] - a[1] - d[1]*sum(c[3:(n+1)]) + (2*eta-1)*b[1] + c[1]^2/(2*r)
    return target[1:(n+1)] 
end

function linear_feasible(d)
    n = length(d)+1
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    a,b,c = compute_parts_from_d(eta,r,n,d)
    
    return rowSumMinusColumnSumMinusTarget(a,b,c,d,n) # lambda*ones(n+2) - lambda'*ones(n+2) - target
end

function newtonStep(d)
    x = d
    n = length(d) + 1
    J = zeros(n+1, n-1)
    for i in 1:7
        F = linear_feasible(x)
        if norm(F)<1e-14
            println("    ",i)
            break
        end
        #J = finite_difference_jacobian(linear_feasible, x)
        ForwardDiff.jacobian!(J, linear_feasible, x) #finite_difference_jacobian(linear_feasible, x)
        Δx = -J \ F  # Solve the linear system J * Δx = -F
        x += Δx      # Update the guess
        println("   Newton Iteration $i: Solution guess: ", norm(F))
    end
    return x
end

function guessNext(d,n) #A simple heuristic for guessing the next solution
    d_next = zeros(n)
    d_next[2:n] = d
    d_next[1] = d[1]
    return d_next
end

function guessNextHistory(d1,d2,d3,d4,d5,step)
    #Guess c0 from the pattern
    int1 = Interpolations.scale(interpolate(d1, BSpline(Quadratic(Line(OnCell())))), 0:(1.0/(length(d1)-1)):1)
    int2 = Interpolations.scale(interpolate(d2, BSpline(Quadratic(Line(OnCell())))), 0:(1.0/(length(d2)-1)):1)
    int3 = Interpolations.scale(interpolate(d3, BSpline(Quadratic(Line(OnCell())))), 0:(1.0/(length(d3)-1)):1)
    int4 = Interpolations.scale(interpolate(d4, BSpline(Quadratic(Line(OnCell())))), 0:(1.0/(length(d4)-1)):1)
    int5 = Interpolations.scale(interpolate(d5, BSpline(Quadratic(Line(OnCell())))), 0:(1.0/(length(d5)-1)):1)
    
    n = length(d1) + step
    d_next = zeros(n)
    for i in 1:n
        t = [1,2,3,4,5]
        s = [int1((i-1.0)/(n-1.0)), int2((i-1.0)/(n-1.0)),int3((i-1.0)/(n-1.0)),int4((i-1.0)/(n-1.0)),int5((i-1.0)/(n-1.0))] 
        p = Polynomials.fit(t, s, 1)
        d_next[i] = max(p(0),0)
    end
    return d_next
end

function finite_difference_jacobian(f, x, epsilon=1e-8) #ForawrdDiff wasnt playing nice with offset arrays
    n = length(x)
    m = length(f(x))
    J = zeros(m, n)

    # Iterate over each input dimension to perturb
    for j in 1:n
        println("       FD: ",j)
        x_forward = copy(x)
        x_backward = copy(x)

        # Perturb the j-th element
        x_forward[j] += epsilon
        x_backward[j] -= epsilon

        # Compute the function values with perturbed inputs
        f_forward = f(x_forward)
        f_backward = f(x_backward)

        # Compute the finite difference approximation for column j
        J[:, j] = (f_forward - f_backward) / (2 * epsilon)
    end

    return J
end
    
function postiveSum(v)
    ret = 0
    for val in v
        ret += max(0,val)
    end
    return ret
end

postiveSum (generic function with 1 method)

# Verify Existing Certificates

In [3]:
println("Verifing Certificates for n=3,4,5,...,2240")
deltaMaximum = 0.0
for n in 3:2200
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    d = CSV.read(string("Conjecture Certificates/",n,"c.csv"), DataFrame).Column
    a,b,c = compute_parts_from_d(eta, r, n, d)
    lambda = recompose(a,b,c,d)
    if minimum(lambda)<0
        println("INFEASIBLE CERTIFICATE: ",n)
    end
    deltaMaximum = postiveSum(linear_feasible(d))
end
println("    Maximum delta: ",deltaMaximum)

Verifing Certificates for n=3,4,5,...,2240
    Maximum delta: 1.7540900372828294e-14


In [4]:
println("Verifing Certificates for n=2240,2560,...,8960")
deltaMaximum = 0.0
for n in 2240:320:8960
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    d = CSV.read(string("Conjecture Certificates/",n,"c.csv"), DataFrame).Column
    a,b,c = compute_parts_from_d(eta, r, n, d)
    lambda = recompose(a,b,c,d)
    if minimum(lambda)<0
        println("INFEASIBLE CERTIFICATE: ",n)
    end
    deltaMaximum = postiveSum(linear_feasible(d))
end
println("    Maximum delta: ",deltaMaximum)

Verifing Certificates for n=2240,2560,...,8960
    Maximum delta: 5.77358053401901e-14


In [5]:
println("Verifing Certificates for n=8960,10560,...,18560")
deltaMaximum = 0.0
for n in 8960:1600:18560
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    d = CSV.read(string("Conjecture Certificates/",n,"c.csv"), DataFrame).Column
    a,b,c = compute_parts_from_d(eta, r, n, d)
    lambda = recompose(a,b,c,d)
    if minimum(lambda)<0
        println("INFEASIBLE CERTIFICATE: ",n)
    end
    deltaMaximum = postiveSum(linear_feasible(d))
end
println("    Maximum delta: ",deltaMaximum)

Verifing Certificates for n=8960,10560,...,18560
    Maximum delta: 1.076808015313107e-13


# Plotting Certificate Components a,b,c,d

In [6]:
plotly()

n=10
eta = compute_eta(n)
r = 1 / (2 * (1 + 2 * n * eta))
d10 =    CSV.read(string("Conjecture Certificates/10c.csv"), DataFrame).Column
a10,b10,c10 = compute_parts_from_d(eta, r, n, d10)

n=100
eta = compute_eta(n)
r = 1 / (2 * (1 + 2 * n * eta))
d100 =   CSV.read(string("Conjecture Certificates/100c.csv"), DataFrame).Column
a100,b100,c100 = compute_parts_from_d(eta, r, n, d100)

n=1000
eta = compute_eta(n)
r = 1 / (2 * (1 + 2 * n * eta))
d1000 =  CSV.read(string("Conjecture Certificates/1000c.csv"), DataFrame).Column
a1000,b1000,c1000 = compute_parts_from_d(eta, r, n, d1000)

n=10560
eta = compute_eta(n)
r = 1 / (2 * (1 + 2 * n * eta))
d10560 = CSV.read(string("Conjecture Certificates/10560c.csv"), DataFrame).Column
a10560,b10560,c10560 = compute_parts_from_d(eta, r, n, d10560);

In [7]:
x10 = range(0, stop=1, length=10)
x100 = range(0, stop=1, length=100)
x1000 = range(0, stop=1, length=1000)
x10560 = range(0, stop=1, length=10560)

plot(x10, a10, label="N=10", title="a_0, ..., a_{N-1}", titlefont=font(14), linewidth=3,  # Thicker lines
    guidefont=font(12), tickfont=font(14), legendfont=font(12), # Larger fonts
    legend=:bottomright, yscale=:log10)
plot!(x100, a100, label="N=100", linewidth=3)
plot!(x1000, a1000, label="N=1000", linewidth=3)
plot!(x10560, a10560, label="N=10560", linewidth=3)

In [8]:
x10 = range(0, stop=1, length=9)
x100 = range(0, stop=1, length=99)
x1000 = range(0, stop=1, length=999)
x10560 = range(0, stop=1, length=10559)

plot(x10, b10, label="N=10", title="b_0, ..., b_{N-2}", titlefont=font(14), linewidth=3,  # Thicker lines
    guidefont=font(12), tickfont=font(14), legendfont=font(12),# Larger fonts
    legend=:bottomright, yscale=:log10)
plot!(x100, b100, label="N=100", linewidth=3)
plot!(x1000, b1000, label="N=1000", linewidth=3)
plot!(x10560, b10560, label="N=10560", linewidth=3)

In [9]:
x10 = range(0, stop=1, length=11)
x100 = range(0, stop=1, length=101)
x1000 = range(0, stop=1, length=1001)
x10560 = range(0, stop=1, length=10561)

plot(x10, c10, label="N=10", title="c_0, ..., c_{N}", titlefont=font(14), linewidth=3,  # Thicker lines
    guidefont=font(12), tickfont=font(14), legendfont=font(12),# Larger fonts
    legend=:bottomright, yscale=:log10)
plot!(x100, c100, label="N=100", linewidth=3)
plot!(x1000, c1000, label="N=1000", linewidth=3)
plot!(x10560, c10560, label="N=10560", linewidth=3)

In [10]:
x10 = range(0, stop=1, length=9)
x100 = range(0, stop=1, length=99)
x1000 = range(0, stop=1, length=999)
x10560 = range(0, stop=1, length=10559)

plot(x10, d10, label="N=10", title="d_0, ..., d_{N-2}", titlefont=font(14), linewidth=3,  # Thicker lines
    guidefont=font(12), tickfont=font(14), legendfont=font(12), # Larger fonts
    legend=:bottomright, yscale=:log10)
plot!(x100, d100, label="N=100", linewidth=3)
plot!(x1000, d1000, label="N=1000", linewidth=3)
plot!(x10560, d10560, label="N=10560", linewidth=3)

# Generate New Certificates via Newton's Method

In [13]:
n = 7
eta = compute_eta(n)
r = 1 / (2 * (1 + 2 * n * eta))

stepSize = 1
x_olderby5 = CSV.read(string("Conjecture Certificates/",n-4*stepSize,"c.csv"), DataFrame).Column
x_olderby4 = CSV.read(string("Conjecture Certificates/",n-3*stepSize,"c.csv"), DataFrame).Column
x_olderby3 = CSV.read(string("Conjecture Certificates/",n-2*stepSize,"c.csv"), DataFrame).Column
x_olderby2 = CSV.read(string("Conjecture Certificates/",n-1*stepSize,"c.csv"), DataFrame).Column
x = CSV.read(string("Conjecture Certificates/",n,"c.csv"), DataFrame).Column

start_time = time()

for t in 8:stepSize:256
    a,b,c = compute_parts_from_d(eta, r, n, x)
    lambda = recompose(a,b,c,x)
    println("Certicate ",n,"  with validation of ", minimum(lambda)>=0, " and ", norm(linear_feasible(x))<=1e-10, ".   its been ", round((time()-start_time)/3600, digits=5), " hours")

    n=t
    xNext = guessNextHistory(x,x_olderby2,x_olderby3,x_olderby4,x_olderby5,stepSize)
    eta = compute_eta(n)
    r = 1 / (2 * (1 + 2 * n * eta))
    xNext = newtonStep(xNext)
    
    df = DataFrame(Column = xNext)
    CSV.write(string("Conjecture Certificates/",n,"c.csv"), df)
    
    x_olderby5 = x_olderby4
    x_olderby4 = x_olderby3
    x_olderby3 = x_olderby2
    x_olderby2 = x
    x = xNext
end

Certicate 7  with validation of true and true.   its been 1.0e-5 hours
   Newton Iteration 1: Solution guess: 0.08294240495273136
   Newton Iteration 2: Solution guess: 0.002453793039438252
   Newton Iteration 3: Solution guess: 1.8276650399319861e-6
   Newton Iteration 4: Solution guess: 8.367253288684263e-13
    5
Certicate 8  with validation of true and true.   its been 0.00139 hours
   Newton Iteration 1: Solution guess: 0.04833409882934135
   Newton Iteration 2: Solution guess: 0.0008367721121480979
   Newton Iteration 3: Solution guess: 2.276509222970793e-7
   Newton Iteration 4: Solution guess: 1.4311360597871267e-14
    5
Certicate 9  with validation of true and true.   its been 0.00167 hours
   Newton Iteration 1: Solution guess: 0.03540959438724231
   Newton Iteration 2: Solution guess: 0.0004646715975992826
   Newton Iteration 3: Solution guess: 7.518714483313978e-8
    4
Certicate 10  with validation of true and true.   its been 0.002 hours
   Newton Iteration 1: Solution g

   Newton Iteration 2: Solution guess: 6.393345998176007e-7
   Newton Iteration 3: Solution guess: 2.6454018190604183e-13
    4
Certicate 46  with validation of true and true.   its been 0.00346 hours
   Newton Iteration 1: Solution guess: 0.0010697970322757593
   Newton Iteration 2: Solution guess: 5.880341538415285e-7
   Newton Iteration 3: Solution guess: 2.250668454673674e-13
    4
Certicate 47  with validation of true and true.   its been 0.00346 hours
   Newton Iteration 1: Solution guess: 0.0010264370942026171
   Newton Iteration 2: Solution guess: 5.418398934129756e-7
   Newton Iteration 3: Solution guess: 1.921641040250556e-13
    4
Certicate 48  with validation of true and true.   its been 0.00347 hours
   Newton Iteration 1: Solution guess: 0.0009857533245751055
   Newton Iteration 2: Solution guess: 5.001579852443633e-7
   Newton Iteration 3: Solution guess: 1.6459356166774427e-13
    4
Certicate 49  with validation of true and true.   its been 0.00347 hours
   Newton Itera

   Newton Iteration 1: Solution guess: 0.0003744481402097439
   Newton Iteration 2: Solution guess: 7.229608961980076e-8
    3
Certicate 81  with validation of true and true.   its been 0.00363 hours
   Newton Iteration 1: Solution guess: 0.00036582398351587463
   Newton Iteration 2: Solution guess: 6.898502199764285e-8
    3
Certicate 82  with validation of true and true.   its been 0.00364 hours
   Newton Iteration 1: Solution guess: 0.00035750347883222404
   Newton Iteration 2: Solution guess: 6.58638557373432e-8
    3
Certicate 83  with validation of true and true.   its been 0.00364 hours
   Newton Iteration 1: Solution guess: 0.0003494695431755807
   Newton Iteration 2: Solution guess: 6.291892560016113e-8
    3
Certicate 84  with validation of true and true.   its been 0.00365 hours
   Newton Iteration 1: Solution guess: 0.0003417096083707476
   Newton Iteration 2: Solution guess: 6.013850466902441e-8
    3
Certicate 85  with validation of true and true.   its been 0.00366 hours

Certicate 122  with validation of true and true.   its been 0.0041 hours
   Newton Iteration 1: Solution guess: 0.00017004817349862883
   Newton Iteration 2: Solution guess: 1.4724709078525211e-8
    3
Certicate 123  with validation of true and true.   its been 0.00413 hours
   Newton Iteration 1: Solution guess: 0.00016747516208848726
   Newton Iteration 2: Solution guess: 1.4278579873603386e-8
    3
Certicate 124  with validation of true and true.   its been 0.00415 hours
   Newton Iteration 1: Solution guess: 0.00016496126479540393
   Newton Iteration 2: Solution guess: 1.3849394051138066e-8
    3
Certicate 125  with validation of true and true.   its been 0.00417 hours
   Newton Iteration 1: Solution guess: 0.00016250470702830076
   Newton Iteration 2: Solution guess: 1.3436385282687385e-8
    3
Certicate 126  with validation of true and true.   its been 0.00419 hours
   Newton Iteration 1: Solution guess: 0.00016010376205809258
   Newton Iteration 2: Solution guess: 1.303882379205

   Newton Iteration 2: Solution guess: 5.054534482434591e-9
    3
Certicate 163  with validation of true and true.   its been 0.00527 hours
   Newton Iteration 1: Solution guess: 9.894216650561918e-5
   Newton Iteration 2: Solution guess: 4.938520277328207e-9
    3
Certicate 164  with validation of true and true.   its been 0.00531 hours
   Newton Iteration 1: Solution guess: 9.781601952316225e-5
   Newton Iteration 2: Solution guess: 4.825846911244228e-9
    3
Certicate 165  with validation of true and true.   its been 0.00535 hours
   Newton Iteration 1: Solution guess: 9.670931870283466e-5
   Newton Iteration 2: Solution guess: 4.7163998801686425e-9
    3
Certicate 166  with validation of true and true.   its been 0.00539 hours
   Newton Iteration 1: Solution guess: 9.562161968956915e-5
   Newton Iteration 2: Solution guess: 4.610068169847363e-9
    3
Certicate 167  with validation of true and true.   its been 0.00543 hours
   Newton Iteration 1: Solution guess: 9.455249668930603e-5

   Newton Iteration 1: Solution guess: 6.557420044115293e-5
   Newton Iteration 2: Solution guess: 2.155911817421668e-9
    3
Certicate 204  with validation of true and true.   its been 0.00754 hours
   Newton Iteration 1: Solution guess: 6.497190031336235e-5
   Newton Iteration 2: Solution guess: 2.116225415754554e-9
    3
Certicate 205  with validation of true and true.   its been 0.00761 hours
   Newton Iteration 1: Solution guess: 6.437798027373638e-5
   Newton Iteration 2: Solution guess: 2.0774556967305515e-9
    3
Certicate 206  with validation of true and true.   its been 0.00768 hours
   Newton Iteration 1: Solution guess: 6.379228647543608e-5
   Newton Iteration 2: Solution guess: 2.0395777346902875e-9
    3
Certicate 207  with validation of true and true.   its been 0.00776 hours
   Newton Iteration 1: Solution guess: 6.321467006980605e-5
   Newton Iteration 2: Solution guess: 2.002566827410251e-9
    3
Certicate 208  with validation of true and true.   its been 0.00783 hour

   Newton Iteration 1: Solution guess: 4.639393280160162e-5
   Newton Iteration 2: Solution guess: 1.0745749196427297e-9
    3
Certicate 245  with validation of true and true.   its been 0.0117 hours
   Newton Iteration 1: Solution guess: 4.603775291222637e-5
   Newton Iteration 2: Solution guess: 1.0580486608334288e-9
    3
Certicate 246  with validation of true and true.   its been 0.01181 hours
   Newton Iteration 1: Solution guess: 4.568571164672163e-5
   Newton Iteration 2: Solution guess: 1.041841271093849e-9
    3
Certicate 247  with validation of true and true.   its been 0.01194 hours
   Newton Iteration 1: Solution guess: 4.5337745625435685e-5
   Newton Iteration 2: Solution guess: 1.0259456792985047e-9
    3
Certicate 248  with validation of true and true.   its been 0.01208 hours
   Newton Iteration 1: Solution guess: 4.499379277986431e-5
   Newton Iteration 2: Solution guess: 1.0103545416929594e-9
    3
Certicate 249  with validation of true and true.   its been 0.0122 hou